In [4]:
import pydeck as pdk
import geopandas as gpd
import pandas as pd
import mapboxgl
import os

In [5]:
# mapbox 토큰을 사용했으며,
# 필자는 매번 토큰을 복사 붙여넣기하기가 번거로워 환경변수에 등록하여 사용함
token = os.getenv('MAPBOX_ACCESS_TOKEN')

In [6]:
# 데이터는 서울 행정동 데이터이다
geo_data = './older_seoul.geojson'

In [7]:
df = gpd.read_file(geo_data)
df.head()

시    구    동     행정동코드     인구    남자     여자  \
0  서울특별시  종로구  사직동  11110530   9700  4375   5325   
1  서울특별시  종로구  삼청동  11110540   3013  1443   1570   
2  서울특별시  종로구  부암동  11110550  10525  5002   5523   
3  서울특별시  종로구  평창동  11110560  18830  8817  10013   
4  서울특별시  종로구  무악동  11110570   8745  4078   4667   

                                            geometry  
0  MULTIPOLYGON (((126.97689 37.57565, 126.97703 ...  
1  MULTIPOLYGON (((126.98269 37.59507, 126.98337 ...  
2  MULTIPOLYGON (((126.97585 37.59656, 126.97359 ...  
3  MULTIPOLYGON (((126.97507 37.63139, 126.97649 ...  
4  MULTIPOLYGON (((126.96067 37.58080, 126.96281 ...

In [8]:
# pydeck은 geometry 컬럼의 shapely.geometry.multipolygon 타입을 읽지 못하여 아래와 같이 변경하는 작업을 해줌
# multipolygon을 polygon들로 변경 후 진행하여야 함

df['polygons'] = df['geometry'].apply(lambda x : list(x.geoms))

def polygon_to_coordinates(x):
    lon, lat = x[0].exterior.xy
    return [[x, y] for x, y in zip(lon, lat)]

df['coordinates'] = df['polygons'].apply(polygon_to_coordinates)
del df['geometry']
del df['polygons']

In [9]:
df.head()

시    구    동     행정동코드     인구    남자     여자  \
0  서울특별시  종로구  사직동  11110530   9700  4375   5325   
1  서울특별시  종로구  삼청동  11110540   3013  1443   1570   
2  서울특별시  종로구  부암동  11110550  10525  5002   5523   
3  서울특별시  종로구  평창동  11110560  18830  8817  10013   
4  서울특별시  종로구  무악동  11110570   8745  4078   4667   

                                         coordinates  
0  [[126.97688884274817, 37.575650779448786], [12...  
1  [[126.98268938649305, 37.5950655194224], [126....  
2  [[126.97585113775686, 37.59656422224408], [126...  
3  [[126.97507466788086, 37.63138628651299], [126...  
4  [[126.96067353273895, 37.580797842029725], [12...

In [10]:
df['정규화인구'] = df['인구'] / df['인구'].max()

In [11]:
# pydeck은 pandas.dataframe에서만 동작해서 변경함
df = pd.DataFrame(df)

In [12]:
layer = pdk.Layer(
    'PolygonLayer', # 사용할 Layer 타입
    df, # 시각화에 쓰일 데이터프레임
    get_polygon='coordinates', # geometry 정보를 담고있는 컬럼 이름
    get_fill_color='[0, 255*정규화인구, 0]', # 각 데이터 별 rgb 또는 rgba 값 (0~255)
    pickable=True, # 지도와 interactive 한 동작 on
    auto_highlight=True # 마우스 오버(hover) 시 박스 출력
)

# Set the viewport location
center = [126.986, 37.565]
view_state = pdk.ViewState(
    longitude=center[0],
    latitude=center[1],
    zoom=10)

# Render
r = pdk.Deck(layers=[layer], 
             initial_view_state=view_state)
r.to_html()

In [13]:
layer = pdk.Layer(
    'PolygonLayer', # 사용할 Layer 타입
    df, # 시각화에 쓰일 데이터프레임
    extruded = True,
    get_elevation = '인구',
    elevation_scale = 0.05,
    get_polygon='coordinates', # geometry 정보를 담고있는 컬럼 이름
    get_fill_color='[0, 255*정규화인구, 0]', # 각 데이터 별 rgb 또는 rgba 값 (0~255)
    pickable=True, # 지도와 interactive 한 동작 on
    auto_highlight=True # 마우스 오버(hover) 시 박스 출력
)

view_state.bearing=15
view_state.pitch=45

r = pdk.Deck(layers=[layer], initial_view_state=view_state)
r.to_html()

In [15]:
coordinates_list = []
for i in range(len(df['coordinates'])):
    for j in range(len(df['coordinates'][i])):
        coordinates_list.append(df['coordinates'][i][j])

In [16]:
coordinates_df = pd.DataFrame(coordinates_list, columns=['lng','lat'])

In [18]:
coordinates_df.head()

lng        lat
0  126.976889  37.575651
1  126.977034  37.569195
2  126.975975  37.569336
3  126.975375  37.569316
4  126.974332  37.569262

In [21]:
layer = pdk.Layer(
    'HexagonLayer',
    coordinates_df,
    get_position='[lng, lat]',
    auto_highlight=True,
    elevation_scale=50,
    pickable=True,
    elevation_range=[0, 3000],
    extruded=True,                 
    coverage=1)
# center = [126.986, 37.565]
view_state = pdk.ViewState(
    longitude=126.986,
    latitude=37.565,
    zoom=6,
    min_zoom=5,
    max_zoom=15,
    pitch=40.5,
    bearing=-27.36)

r = pdk.Deck(layers=[layer], initial_view_state=view_state)
r.to_html()